In [54]:
import json

from lxml import etree
from tqdm import tqdm

In [55]:
namespaces = {
    'rdf': 'http://www.w3.org/1999/02/22-rdf-syntax-ns#',
    'res': 'http://purl.org/vocab/resourcelist/schema#',
    'z': 'http://www.zotero.org/namespaces/export#',
    'ctag': 'http://commontag.org/ns#',
    'dcterms': 'http://purl.org/dc/terms/',
    'bibo': 'http://purl.org/ontology/bibo/',
    'foaf': 'http://xmlns.com/foaf/0.1/',
    'address': 'http://schemas.talis.com/2005/address/schema#'
}

In [56]:
with open('bibliographic_data.rdf', 'r', encoding='utf-8') as file:
    xml_content = file.read()

root = etree.fromstring(xml_content)

## File-wide lookup

In [57]:
author_lookup = {}
persons = root.findall('.//foaf:Person', namespaces=namespaces)

for person in persons:
    node_id = person.get('{http://www.w3.org/1999/02/22-rdf-syntax-ns#}nodeID')
    if not node_id:
        continue

    given_name = person.find('foaf:givenName', namespaces=namespaces)
    surname = person.find('foaf:surname', namespaces=namespaces)

    
    
    person_str = ''
    if surname is not None:
        person_str += surname.text
        if given_name is not None:
            person_str += ', ' + given_name.text
    
    author_lookup[node_id] = person_str

In [58]:
keyword_lookup = {}
user_tags = root.findall('.//ctag:UserTag', namespaces=namespaces)
for user_tag in user_tags:
    node_id = user_tag.get('{http://www.w3.org/1999/02/22-rdf-syntax-ns#}nodeID')
    if not node_id:
        continue

    label = user_tag.find('ctag:label', namespaces=namespaces)
    if label is not None:
        keyword_lookup[node_id] = label.text

keyword_lookup

{'n13': 'annotatie',
 'n15': 'Rijksmuseum',
 'n23': 'recensie',
 'n31': 'Deken, Aagje',
 'n32': 'literatuur en economie',
 'n33': 'Wolff, Betje',
 'n41': 'kolonialisme',
 'n42': 'papier',
 'n43': 'Valentijn, François',
 'n44': 'Verenigde Oostindische Compagnie (VOC)',
 'n52': 'religieuze symboliek',
 'n53': 'zeventiende eeuw',
 'n61': 'astrologie',
 'n65': 'Rumphius, Georg Everard',
 'n66': 'taxonomie',
 'n74': 'Allard Pierson',
 'n75': 'Reformatie',
 'n76': 'roofdruk',
 'n85': 'alchemie',
 'n87': 'geneeskundig traktaat',
 'n104': 'archiefonderzoek',
 'n113': 'mystiek',
 'n114': 'spiritualiteit',
 'n116': 'zestiende eeuw',
 'n124': 'Amerika',
 'n125': 'drukkersgeschiedenis',
 'n126': 'uitgeverijgeschiedenis',
 'n147': 'boekgeschiedenis',
 'n148': 'incunabelen',
 'n163': 'getijdenboek',
 'n164': 'Grote, Geert',
 'n172': 'beeld en tekst',
 'n196': 'hermetisme',
 'n212': 'achttiende eeuw',
 'n213': 'zelfrepresentatie',
 'n214': 'auteurschap',
 'n215': 'vertaler',
 'n216': 'vertaling',
 'n

In [59]:
def parse_keywords(z_node):
    keywords = []

    tagged_elements = z_node.findall('.//ctag:tagged', namespaces=namespaces)
    for tagged in tagged_elements:
        node_id = tagged.get('{http://www.w3.org/1999/02/22-rdf-syntax-ns#}nodeID')
        if node_id and node_id in keyword_lookup:
            keywords.append(keyword_lookup[node_id])

        user_tag = tagged.find('ctag:UserTag/ctag:label', namespaces=namespaces)
        if user_tag is not None:
            keywords.append(user_tag.text)

    return {'KW': keywords}

### Journal articles

In [60]:
def parse_academic_article(article):
    bibo_info = {}

    authors = []
    author_list = article.find('.//rdf:Seq', namespaces=namespaces)
    if author_list is not None:
        for li in author_list.findall('rdf:li', namespaces=namespaces):
            node_id = li.get('{http://www.w3.org/1999/02/22-rdf-syntax-ns#}nodeID')
            if node_id in author_lookup:
                authors.append(author_lookup[node_id])
    if authors:
        bibo_info['AU'] = authors

    extra_node = article.find('{http://www.zotero.org/namespaces/export#}extra', namespaces=namespaces)
    if extra_node is not None:
        bibo_info['N1'] = extra_node.text

    title_node = article.find('{http://purl.org/dc/terms/}title')
    if title_node is not None:
        bibo_info['TI'] = title_node.text

    uri_node = article.find('{http://purl.org/ontology/bibo/}uri')
    if uri_node is not None:
        bibo_info['UR'] = uri_node.text
    
    abstract_node = article.find('{http://purl.org/dc/terms/}abstract')
    if abstract_node is not None:
        bibo_info['AB'] = abstract_node.text
    
    pages_node = article.find('{http://purl.org/ontology/bibo/}pages')
    if pages_node is not None:
        pages = pages_node.text.split('-')
        if len(pages) == 2:
            start_page, end_page = pages
        else:
            start_page = end_page = pages[0]
        bibo_info['SP'] = start_page
        bibo_info['EP'] = end_page
    
    doi_node = article.find('{http://purl.org/ontology/bibo/}doi')
    if doi_node is not None:
        bibo_info['DO'] = doi_node.text
    
    language_node = article.find('{http://purl.org/dc/terms/}language')
    if language_node is not None:
        bibo_info['LA'] = language_node.text

    issue_node = article.find('.//{http://purl.org/ontology/bibo/}Issue', namespaces=namespaces)
    if issue_node is not None:
        year_node = issue_node.find('{http://purl.org/dc/terms/}date', namespaces=namespaces)
        if year_node is not None:
            bibo_info['PY'] = year_node.text

        volume_node = issue_node.find('{http://purl.org/ontology/bibo/}volume', namespaces=namespaces)
        if volume_node is not None:
            bibo_info['VL'] = volume_node.text

        issue_num_node = issue_node.find('{http://purl.org/ontology/bibo/}issue', namespaces=namespaces)
        if issue_num_node is not None:
            bibo_info['IS'] = issue_num_node.text

    journal_node = article.find('.//{http://purl.org/ontology/bibo/}Journal')
    if journal_node is not None:
        journal_title_node = journal_node.find('{http://purl.org/dc/terms/}title')
        if journal_title_node is not None:
            bibo_info['T2'] = journal_title_node.text
        
        issn_node = journal_node.find('{http://purl.org/ontology/bibo/}issn')
        if issn_node is not None:
            bibo_info['SN'] = issn_node.text

        theme_node = journal_node.find('.//{http://purl.org/ontology/bibo/}Series')
        if theme_node is not None:
            theme_title_node = theme_node.find('{http://purl.org/dc/terms/}title')
            if theme_title_node is not None:
                bibo_info['T3'] = theme_title_node.text
   
    return bibo_info
    
def parse_jour(z_node):
    info = {}

    bibo_node = None
    if z_node.getnext() is not None and z_node.getnext().tag == '{' + namespaces['bibo'] + '}AcademicArticle':
        bibo_node = z_node.getnext()
    else:
        resource_node = z_node.find('{http://purl.org/vocab/resourcelist/schema#}resource')
        if resource_node is not None:
            bibo_node = resource_node.find('{http://purl.org/ontology/bibo/}AcademicArticle')
        else:
            bibo_node = z_node.find('{http://purl.org/ontology/bibo/}AcademicArticle')  # fallback
    
    if bibo_node is not None:
        info.update(parse_academic_article(bibo_node))
    
    info.update(parse_keywords(z_node))

    return info

### Full books

In [61]:
def parse_bibo_book(book):
    bibo_info = {}

    authors = []
    author_list = book.find('.//bibo:authorList/rdf:Seq', namespaces=namespaces)
    if author_list is not None:
        for li in author_list.findall('rdf:li', namespaces=namespaces):
            node_id = li.get('{http://www.w3.org/1999/02/22-rdf-syntax-ns#}nodeID')
            if node_id in author_lookup:
                authors.append(author_lookup[node_id])
    if authors:
        bibo_info['AU'] = authors

    editors = []
    editor_list = book.find('.//bibo:editorList/rdf:Seq', namespaces=namespaces)
    if editor_list is not None:
        for li in editor_list.findall('rdf:li', namespaces=namespaces):
            node_id = li.get('{http://www.w3.org/1999/02/22-rdf-syntax-ns#}nodeID')
            if node_id in author_lookup:
                editors.append(author_lookup[node_id])

    if editors:
        bibo_info['A3'] = editors

    extra_node = book.find('{http://www.zotero.org/namespaces/export#}extra', namespaces=namespaces)
    if extra_node is not None:
        bibo_info['N1'] = extra_node.text

    title_node = book.find('{http://purl.org/dc/terms/}title')
    if title_node is not None:
        bibo_info['TI'] = title_node.text

    date_node = book.find('{http://purl.org/dc/terms/}date')
    if date_node is not None:
        bibo_info['PY'] = date_node.text

    uri_node = book.find('{http://purl.org/ontology/bibo/}uri')
    if uri_node is not None:
        bibo_info['UR'] = uri_node.text
    
    abstract_node = book.find('{http://purl.org/dc/terms/}abstract')
    if abstract_node is not None:
        bibo_info['AB'] = abstract_node.text
    
    pages_node = book.find('{http://purl.org/ontology/bibo/}numPages')
    if pages_node is not None:
        bibo_info['SP'] = pages_node.text
    
    isbn_nodes = book.findall('{http://purl.org/ontology/bibo/}isbn13')
    if isbn_nodes is not None:
        bibo_info['SN'] = ' '.join([inode.text for inode in isbn_nodes])
    
    doi_node = book.find('{http://purl.org/ontology/bibo/}doi')
    if doi_node is not None:
        bibo_info['DO'] = doi_node.text
    
    language_node = book.find('{http://purl.org/dc/terms/}language')
    if language_node is not None:
        bibo_info['LA'] = language_node.text

    volume_node = book.find('{http://purl.org/ontology/bibo/}volume')
    if volume_node is not None:
        bibo_info['VL'] = volume_node.text

    series_node = book.find('.//{http://purl.org/ontology/bibo/}Series', namespaces=namespaces)
    if series_node is not None:
        series_title_node = series_node.find('{http://purl.org/dc/terms/}title', namespaces=namespaces)
        if series_title_node is not None:
            bibo_info['T3'] = series_title_node.text
        series_number_node = series_node.find('{http://purl.org/ontology/bibo/}number', namespaces=namespaces)
        if series_number_node is not None:
            bibo_info['M1'] = series_number_node.text

    publisher_node = book.find('{http://purl.org/dc/terms/}publisher/foaf:Organization', namespaces=namespaces)
    if publisher_node is not None:
        publisher_name_node = publisher_node.find('{http://xmlns.com/foaf/0.1/}name', namespaces=namespaces)
        locality_node = publisher_node.find('{http://schemas.talis.com/2005/address/schema#}localityName', namespaces=namespaces)

        if publisher_name_node is not None:
            bibo_info['PB'] = publisher_name_node.text
        if locality_node is not None:
            bibo_info['CY'] = locality_node.text
   
    return bibo_info
    
def parse_book(z_node):
    info = {}

    bibo_node = None
    if z_node.getnext() is not None and z_node.getnext().tag == '{' + namespaces['bibo'] + '}Book':
        bibo_node = z_node.getnext()
    else:
        resource_node = z_node.find('{http://purl.org/vocab/resourcelist/schema#}resource')
        if resource_node is not None:
            bibo_node = resource_node.find('{http://purl.org/ontology/bibo/}Book')
        else:
            bibo_node = z_node.find('{http://purl.org/ontology/bibo/}Book')
    
    if bibo_node is not None:
        info.update(parse_bibo_book(bibo_node))
    
    info.update(parse_keywords(z_node))

    return info

### Chapters

In [64]:
def parse_bibo_chapter(chapter):
    bibo_info = {}

    # Extract chapter authors
    authors = []
    author_list = chapter.find('.//bibo:authorList/rdf:Seq', namespaces=namespaces)
    if author_list is not None:
        for li in author_list.findall('rdf:li', namespaces=namespaces):
            node_id = li.get('{http://www.w3.org/1999/02/22-rdf-syntax-ns#}nodeID')
            if node_id in author_lookup:
                authors.append(author_lookup[node_id])
    if authors:
        bibo_info['AU'] = authors

    # Extract book editors
    editors = []
    editor_list = chapter.find('.//bibo:editorList/rdf:Seq', namespaces=namespaces)
    if editor_list is not None:
        for li in editor_list.findall('rdf:li', namespaces=namespaces):
            node_id = li.get('{http://www.w3.org/1999/02/22-rdf-syntax-ns#}nodeID')
            if node_id in author_lookup:
                editors.append(author_lookup[node_id])
    if editors:
        bibo_info['A3'] = editors

    # Additional metadata
    extra_node = chapter.find('{http://www.zotero.org/namespaces/export#}extra', namespaces=namespaces)
    if extra_node is not None:
        bibo_info['N1'] = extra_node.text

    # Chapter title
    title_node = chapter.find('{http://purl.org/dc/terms/}title')
    if title_node is not None:
        bibo_info['TI'] = title_node.text

    # Chapter publication year
    date_node = chapter.find('{http://purl.org/dc/terms/}date')
    if date_node is not None:
        bibo_info['PY'] = date_node.text

    # URI
    uri_node = chapter.find('{http://purl.org/ontology/bibo/}uri')
    if uri_node is not None:
        bibo_info['UR'] = uri_node.text
    
    # Abstract
    abstract_node = chapter.find('{http://purl.org/dc/terms/}abstract')
    if abstract_node is not None:
        bibo_info['AB'] = abstract_node.text
    
    # Pages
    pages_node = chapter.find('{http://purl.org/ontology/bibo/}pages')
    if pages_node is not None:
        pages = pages_node.text.split('-')
        if len(pages) == 2:
            bibo_info['SP'] = pages[0]
            bibo_info['EP'] = pages[1]
    
    # ISBNs
    isbn_nodes = chapter.findall('{http://purl.org/ontology/bibo/}isbn13')
    if isbn_nodes:
        bibo_info['SN'] = ' '.join([inode.text for inode in isbn_nodes])
    
    # DOI
    doi_node = chapter.find('{http://purl.org/ontology/bibo/}doi')
    if doi_node is not None:
        bibo_info['DO'] = doi_node.text
    
    # Language
    language_node = chapter.find('{http://purl.org/dc/terms/}language')
    if language_node is not None:
        bibo_info['LA'] = language_node.text

    # Volume
    volume_node = chapter.find('{http://purl.org/ontology/bibo/}volume')
    if volume_node is not None:
        bibo_info['VL'] = volume_node.text

    # Series title and number
    series_node = chapter.find('.//{http://purl.org/ontology/bibo/}Series', namespaces=namespaces)
    if series_node is not None:
        series_title_node = series_node.find('{http://purl.org/dc/terms/}title', namespaces=namespaces)
        if series_title_node is not None:
            bibo_info['T3'] = series_title_node.text
        series_number_node = series_node.find('{http://purl.org/ontology/bibo/}number', namespaces=namespaces)
        if series_number_node is not None:
            bibo_info['M1'] = series_number_node.text

    # Extract information about the edited book this chapter is part of
    edited_book_node = chapter.find('.//bibo:EditedBook', namespaces=namespaces)
    if edited_book_node is not None:
        # Extract title of the edited book
        edited_book_title_node = edited_book_node.find('{http://purl.org/dc/terms/}title', namespaces=namespaces)
        if edited_book_title_node is not None:
            bibo_info['T2'] = edited_book_title_node.text  # T2 for book title

        # Extract year of publication for the edited book
        edited_book_year_node = edited_book_node.find('{http://purl.org/dc/terms/}date', namespaces=namespaces)
        if edited_book_year_node is not None:
            bibo_info['PY'] = edited_book_year_node.text  # PY for year of publication

        # Extract ISBN
        isbn_node = edited_book_node.find('{http://purl.org/ontology/bibo/}isbn13', namespaces=namespaces)
        if isbn_node is not None:
            bibo_info['SN'] = isbn_node.text  # SN for ISBN

        # Extract publisher details (name and location)
        publisher_node = edited_book_node.find('{http://purl.org/dc/terms/}publisher/foaf:Organization', namespaces=namespaces)
        if publisher_node is not None:
            publisher_name_node = publisher_node.find('{http://xmlns.com/foaf/0.1/}name', namespaces=namespaces)
            locality_node = publisher_node.find('{http://schemas.talis.com/2005/address/schema#}localityName', namespaces=namespaces)

            if publisher_name_node is not None:
                bibo_info['PB'] = publisher_name_node.text  # PB for publisher name
            if locality_node is not None:
                bibo_info['CY'] = locality_node.text  # CY for city
   
    return bibo_info


def parse_chapter(z_node):
    info = {}
    bibo_node = None
    if z_node.getnext() is not None and z_node.getnext().tag == '{' + namespaces['bibo'] + '}BookSection':
        bibo_node = z_node.getnext()
    else:
        resource_node = z_node.find('{http://purl.org/vocab/resourcelist/schema#}resource')
        if resource_node is not None:
            bibo_node = resource_node.find('{http://purl.org/ontology/bibo/}BookSection')
        else:
            bibo_node = z_node.find('{http://purl.org/ontology/bibo/}BookSection')
    
    if bibo_node is not None:
        info.update(parse_bibo_chapter(bibo_node))
    
    info.update(parse_keywords(z_node))

    return info


In [65]:
user_items = tuple(root.xpath('//z:UserItem', namespaces=namespaces))
for z_node in tqdm(user_items):
    info = {}
    user_item_url = z_node.xpath('@rdf:about', namespaces=namespaces)
    if user_item_url:
        info['ID'] = user_item_url[0]
    else:
        continue

    access_date_node = z_node.find('{http://www.zotero.org/namespaces/export#}accessDate', namespaces=namespaces)
    if access_date_node is not None:
        info['Y2'] = access_date_node.text

    #if info['ID'] != "http://zotero.org/groups/5376439/items/8QEWJVZA":
    #    continue
    
    if z_node.getnext().tag == '{' + namespaces['bibo'] + '}AcademicArticle' or \
       z_node.xpath('.//bibo:AcademicArticle', namespaces=namespaces):
        info.update(parse_jour(z_node))
        info['TY'] = 'JOUR'
    
    elif z_node.getnext().tag == '{' + namespaces['bibo'] + '}Book' or \
       z_node.xpath('.//bibo:Book', namespaces=namespaces):
        info.update(parse_book(z_node))
        info['TY'] = 'BOOK'

    elif z_node.getnext().tag == '{' + namespaces['bibo'] + '}BookSection' or \
       z_node.xpath('.//bibo:BookSection', namespaces=namespaces):
        info.update(parse_chapter(z_node))
        info['TY'] = 'CHAP'
    
    print(json.dumps(info, indent=2))



 24%|██▍       | 2561/10764 [00:00<00:00, 12626.29it/s]

{
  "ID": "http://zotero.org/groups/5376439/items/KFEGCKYY",
  "Y2": "2024-03-11 11:51:41",
  "AU": [
    "Hoek, Myriam van der"
  ],
  "TI": "Een bericht van de uitgever op een tekening van Matthijs Balen",
  "UR": "https://www.aup-online.com/content/journals/10.5117/DBW2022.2.014.HOEK",
  "AB": "In de rubriek: Ingeprent.",
  "SP": "68",
  "EP": "69",
  "DO": "10.5117/DBW2022.2.014.HOEK",
  "LA": "nl",
  "PY": "2022",
  "VL": "38",
  "IS": "2",
  "T2": "De Boekenwereld",
  "SN": "0168-8391, 2949-7019",
  "T3": "Speciaal nummer: Hermetisme",
  "KW": [
    "annotatie",
    "Balen, Matthijs",
    "Rijksmuseum"
  ],
  "TY": "JOUR"
}
{
  "ID": "http://zotero.org/groups/5376439/items/R2I66BQ2",
  "Y2": "2024-03-11 11:51:19",
  "AU": [
    "Moss, Alan"
  ],
  "TI": "[Marijke van der Wal. Koopmanszoon Michiel Heusch op Itali\u00ebreis. Brieven van het thuisfront, 1664-1665",
  "UR": "https://emlc-journal.org/article/view/7262",
  "SP": "150",
  "EP": "152",
  "DO": "10.18352/emlc.135",
  "PY"

 36%|███▌      | 3824/10764 [00:00<00:00, 11626.18it/s]

{
  "ID": "http://zotero.org/groups/5376439/items/TDDD9ECX",
  "AU": [
    "Sijens, Doeke"
  ],
  "N1": "Over: Vestdijk, Simon. De onmogelijke moord. Amsterdam: Bezige Bij, 1966.",
  "TI": "Zoektocht naar Jannie",
  "UR": "https://www.tzum.info/2021/03/recensie-simon-vestdijk-de-onmogelijke-moord/",
  "PY": "2021",
  "VL": "geplaatst op 26.03.2021",
  "T2": "Tzum",
  "KW": [
    "Vestdijk, Simon"
  ],
  "TY": "JOUR"
}
{
  "ID": "http://zotero.org/groups/5376439/items/9YN7E84H",
  "AU": [
    "Jong, Jan de"
  ],
  "N1": "Over: Vos, Marjoleine de. Hoe verschillig. Amsterdam: Van Oorschot, 2021.",
  "TI": "Een beetje blue de ochtend in",
  "UR": "https://www.tzum.info/2021/03/recensie-marjoleine-de-vos-hoe-verschillig/",
  "PY": "2021",
  "VL": "geplaatst op 26.03.2021",
  "T2": "Tzum",
  "KW": [
    "Vos, Marjoleine de"
  ],
  "TY": "JOUR"
}
{
  "ID": "http://zotero.org/groups/5376439/items/AEJ7PBP5",
  "AU": [
    "Ohlsen, Ronald"
  ],
  "N1": "Over:  Vestdijk, Simon. Een Alpenroman; me

 59%|█████▉    | 6335/10764 [00:00<00:00, 11461.85it/s]

{
  "ID": "http://zotero.org/groups/5376439/items/6Q45WAMQ",
  "AU": [
    "Bulck, Gaston van"
  ],
  "N1": "P. 24 Bibliografie; p. 24 Verwijzingen.",
  "TI": "Drankmisbruik en drankverslaving in enkele negentiende-eeuwse Antwerpse volksverhalen",
  "SP": "17",
  "EP": "24",
  "PY": "2017",
  "VL": "54",
  "IS": "1",
  "T2": "Heemkunde Gouw Antwerpen",
  "KW": [
    "Conscience, Hendrik",
    "Baeckelmans, Lode",
    "Buerbaum, Jozef",
    "Sleeckx, Domien"
  ],
  "TY": "JOUR"
}
{
  "ID": "http://zotero.org/groups/5376439/items/IE55H2FU",
  "AU": [
    "Belleghem, Doenja van"
  ],
  "N1": "Onderdeel van de kroniek.",
  "TI": "\"Sacred books | Secret libraries\": een pioniersproject rond religieus erfgoed",
  "SP": "167",
  "EP": "169",
  "PY": "2020",
  "VL": "157",
  "IS": "1",
  "T2": "Handelingen van het Genootschap voor Geschiedenis te Brugge",
  "KW": [
    "religieuze literatuur",
    "Brugge",
    "handschriftenverzameling"
  ],
  "TY": "JOUR"
}
{
  "ID": "http://zotero.org/grou

 81%|████████▏ | 8753/10764 [00:00<00:00, 11333.97it/s]

{
  "ID": "http://zotero.org/groups/5376439/items/FD69CEAZ",
  "AU": [
    "Rompaey, Andreas van"
  ],
  "TI": "Depeuter, Frans: Depeuter als heibelmaker",
  "SP": "64",
  "EP": "83",
  "T2": "De literaire roeping: een inkijk in het werk en leven van enkele belangrijke Nederlandse en Vlaamse auteurs",
  "PY": "2023",
  "SN": "978-94-91545-65-8",
  "PB": "Les iles",
  "CY": "Berchem",
  "KW": [
    "Depeuter, Frans"
  ],
  "TY": "CHAP"
}
{
  "ID": "http://zotero.org/groups/5376439/items/QGJ25AHN",
  "AU": [
    "Rompaey, Andreas van"
  ],
  "TI": "Stefaan van den Bremt: en carri\u00e8reoverzicht",
  "SP": "22",
  "EP": "39",
  "T2": "De literaire roeping: een inkijk in het werk en leven van enkele belangrijke Nederlandse en Vlaamse auteurs",
  "PY": "2023",
  "SN": "978-94-91545-65-8",
  "PB": "Les iles",
  "CY": "Berchem",
  "KW": [
    "Bremt, Stefaan van den"
  ],
  "TY": "CHAP"
}
{
  "ID": "http://zotero.org/groups/5376439/items/ATJA6IQ4",
  "AU": [
    "Remarque, Charlotte"
  ],
  

100%|██████████| 10764/10764 [00:00<00:00, 11716.92it/s]

{
  "ID": "http://zotero.org/groups/5376439/items/W9MPIT43",
  "AU": [
    "Hart, Kees 't"
  ],
  "TI": "En daarna een broodje kaas",
  "AB": "Over: Boer, Bianca. Draaidagen: roman. Amsterdam: Atlas Contact, 2019.",
  "SP": "58",
  "EP": "58",
  "PY": "2019",
  "VL": "143",
  "IS": "35",
  "T2": "De groene Amsterdammer",
  "SN": "1871-7837",
  "KW": [
    "Boer, Bianca"
  ],
  "TY": "JOUR"
}
{
  "ID": "http://zotero.org/groups/5376439/items/M6RDIMF2",
  "AU": [
    "Hart, Kees 't"
  ],
  "TI": "Zomerlezen: de mannenleeslijst (8): de morele remmen gaan los",
  "AB": "Over: Vestdijk, Simon. Op afbetaling. Amsterdam: De Bezige Bij, 1952.",
  "SP": "42",
  "EP": "43",
  "PY": "2019",
  "VL": "143",
  "IS": "35",
  "T2": "De groene Amsterdammer",
  "SN": "1871-7837",
  "KW": [
    "Vestdijk, Simon"
  ],
  "TY": "JOUR"
}
{
  "ID": "http://zotero.org/groups/5376439/items/EKWTU7NX",
  "AU": [
    "Pruis, Marja"
  ],
  "TI": "Weerloze macho",
  "AB": "Over: Jong, Oek de. Zwarte schuur: roman. A